1 пункт

In [ ]:
import os
os.chdir('/content/drive/MyDrive/Colab Notebooks/IS_LR4')

In [ ]:
import tensorflow as tf
device_name = tf.test.gpu_device_name()
if device_name != '/device:GPU:0':
  raise SystemError('GPU device not found')
print('Found GPU at: {}'.format(device_name))

2 пункт

In [ ]:
# загрузка датасета
from keras.datasets import imdb
vocabulary_size = 5000
index_from = 3
(X_train, y_train), (X_test, y_test) = imdb.load_data(path="imdb.npz",
num_words=vocabulary_size,
skip_top=0,
maxlen=None,
seed=19,
start_char=1,
oov_char=2,
index_from=index_from
)

In [ ]:
print("Размер обучающего множества X_train:", X_train.shape)
print("Размер обучающих меток y_train:", y_train.shape)
print("Размер тестового множества X_test:", X_test.shape)
print("Размер тестовых меток y_test:", y_test.shape)

3 пункт

In [ ]:
# создание словаря для перевода индексов в слова
# заргузка словаря "слово:индекс"
word_to_id = imdb.get_word_index()
# уточнение словаря
word_to_id = {key:(value + index_from) for key,value in word_to_id.items()}
word_to_id["<PAD>"] = 0
word_to_id["<START>"] = 1
word_to_id["<UNK>"] = 2
word_to_id["<UNUSED>"] = 3
# создание обратного словаря "индекс:слово"
id_to_word = {value:key for key,value in word_to_id.items()}

In [ ]:
idx = 19
review_indices = X_train[idx]
print("Отзыв в виде индексов:\n", review_indices)

review_text = " ".join(id_to_word.get(i, "?") for i in review_indices)
print("\nОтзыв в виде текста:\n", review_text)

print("\nДлина отзыва (количество индексов):", len(review_indices))

label = y_train[idx]
class_name = "Positive" if label == 1 else "Negative"
print("Метка класса:", label, "| Класс:", class_name)


4 пункт

In [ ]:
print("Максимальная длина отзыва:", len(max(X_train, key=len)))
print("Минимальная длина отзыва:", len(min(X_train, key=len)))

5 пункт

In [ ]:
# предобработка данных
from tensorflow.keras.utils import pad_sequences
max_words = 500
X_train = pad_sequences(X_train, maxlen=max_words, value=0, padding='pre', truncating='post')
X_test = pad_sequences(X_test, maxlen=max_words, value=0, padding='pre', truncating='post')



6 пункт

In [ ]:
print("Максимальная длина отзыва после предобработки:", len(max(X_train, key=len)))
print("Минимальная длина отзыва после предобработки:", len(min(X_train, key=len)))

7 пункт


In [ ]:
idx = 19
review_indices = X_train[idx]
print("Отзыв в виде индексов:\n", review_indices)

review_text = " ".join(id_to_word.get(i, "?") for i in review_indices)
print("\nОтзыв в виде текста:\n", review_text)

print("\nДлина отзыва (количество индексов):", len(review_indices))

label = y_train[idx]
class_name = "Positive" if label == 1 else "Negative"
print("Метка класса:", label, "| Класс:", class_name)

8 пункт

In [ ]:

print("Предобработанное обучающее множество X_train (первые 5 примеров):")
print(X_train[:5])

print("\nПредобработанное тестовое множество X_test (первые 5 примеров):")
print(X_test[:5])


print("Размер обучающего множества X_train:", X_train.shape)
print("Размер обучающих меток y_train:", y_train.shape)
print("Размер тестового множества X_test:", X_test.shape)
print("Размер тестовых меток y_test:", y_test.shape)

9 пункт

In [ ]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dropout, Dense


model = Sequential()
model.add(Embedding(input_dim=vocabulary_size, output_dim=32, input_length=max_words))
model.add(LSTM(64))
model.add(Dropout(0.5))
model.add(Dense(1, activation='sigmoid'))


model.compile(
    optimizer='adam',
    loss='binary_crossentropy',
    metrics=['accuracy']
)

model.build(input_shape=(None, max_words))
model.summary()

In [ ]:
# Обучение модели
history = model.fit(
    X_train,
    y_train,
    epochs=5,
    batch_size=64,
    validation_split=0.2,
    verbose=1
)

In [ ]:
print("\nКачество обучения по эпохам")
for i in range(5):
    train_acc = history.history['accuracy'][i]
    val_acc = history.history['val_accuracy'][i]
    print(f"Эпоха {i+1}: accuracy = {train_acc:.4f}, val_accuracy = {val_acc:.4f}")

10 пункт

In [ ]:
test_loss, test_accuracy = model.evaluate(X_test, y_test, verbose=0)

print("Качество классификации на тестовой выборке")
print(f"Test accuracy: {test_accuracy:.4f}")

In [ ]:
y_score = model.predict(X_test)
y_pred = [1 if y_score[i,0]>=0.5 else 0 for i in range(len(y_score))]
from sklearn.metrics import classification_report
print(classification_report(y_test, y_pred, labels = [0, 1], target_names=['Negative', 'Positive']))

In [ ]:
from sklearn.metrics import roc_curve, auc
import matplotlib.pyplot as plt
fpr, tpr, thresholds = roc_curve(y_test, y_score)
plt.plot(fpr, tpr)
plt.grid()
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive Rate')
plt.title('ROC')
plt.show()
print('Area under ROC is', auc(fpr, tpr))